In [3]:
### IMPORT STATEMENTS ###

import torch
import torch.nn as nn
import torch.optim as optim
from torch.autograd import Variable
import numpy as np
import pandas as pd
import os
import time
import matplotlib.pyplot as plt
import string
from models import *
from configs import cfg
from nltk.translate import bleu_score

In [4]:
### HELPER FUNCTIONS ###

# returns a pandas dataframe of the given file
def load_data(fname):
    return pd.read_csv(fname)


def process_train_data(data):
    # TODO: Input is a pandas DataFrame and return a numpy array (or a torch Tensor/ Variable)
    # that has all features (including characters in one hot encoded form).
    raise NotImplementedError

    
def train_valid_split(data, labels):
    # TODO: Takes in train data and labels as numpy array (or a torch Tensor/ Variable) and
    # splits it into training and validation data.
    raise NotImplementedError
    
    
def process_test_data(data):
    # TODO: Takes in pandas DataFrame and returns a numpy array (or a torch Tensor/ Variable)
    # that has all input features. Note that test data does not contain any review so you don't
    # have to worry about one hot encoding the data.
    raise NotImplementedError

# pads the reviews so that all reviews in the set have an equal size
# also adds the <SOS> and <EOS> tags to the beginning and end of the reviews
# expects a list of reviews where the characters in the reviews are converted into their respective index
# outputs a 2d numpy array of character indices of the reviews
def pad_data(orig_data):
    # defines the character indices for the <SOS>, <EOS>, and <PAD> tags
    sos_tag_index = len(cfg['char_list'])
    eos_tag_index = sos_tag_index + 1
    pad_tag_index = eos_tag_index + 1
    
    # finds the longest review length
    review_lengths = [len(review) for review in orig_data]
    longest_review_length = np.max(review_lengths)
    
    # pads the reviews and adds the <SOS> and <EOS> tags
    padded_reviews = []
    for review in orig_data:
        pad_length = longest_review_length - len(review)
        padded_review = [sos_tag_index] + review + [eos_tag_index] + [pad_tag_index] * pad_length
        padded_reviews.append(padded_review)
        
    return np.array(padded_reviews)

def train(model, X_train, y_train, X_valid, y_valid, cfg):
    # TODO: Train the model!
    raise NotImplementedError
    
    
def generate(model, X_test, cfg):
    # TODO: Given n rows in test data, generate a list of n strings, where each string is the review
    # corresponding to each input row in test data.
    raise NotImplementedError
    
    
def save_to_file(outputs, fname):
    # TODO: Given the list of generated review outputs and output file name, save all these reviews to
    # the file in .txt format.
    raise NotImplementedError


In [5]:
train_data_fname = "Beeradvocate_Train_Short.csv"
test_data_fname = "Beeradvocate_Test_Short"
out_fname = "Output_Reviews.txt"

'''
train_data = load_data(train_data_fname) # Generating the pandas DataFrame
test_data = load_data(test_data_fname) # Generating the pandas DataFrame
train_data, train_labels = process_train_data(train_data) # Converting DataFrame to numpy array
X_train, y_train, X_valid, y_valid = train_valid_split(train_data, train_labels) # Splitting the train data into train-valid data
X_test = process_test_data(test_data) # Converting DataFrame to numpy array

model = baselineLSTM(cfg) # Replace this with model = <your model name>(cfg)
if cfg['cuda']:
    computing_device = torch.device("cuda")
else:
    computing_device = torch.device("cpu")
model.to(computing_device)

train(model, X_train, y_train, X_valid, y_valid, cfg) # Train the model
outputs = generate(model, X_test, cfg) # Generate the outputs for test data
save_to_file(outputs, out_fname) # Save the generated outputs to a file
'''

'\ntrain_data = load_data(train_data_fname) # Generating the pandas DataFrame\ntest_data = load_data(test_data_fname) # Generating the pandas DataFrame\ntrain_data, train_labels = process_train_data(train_data) # Converting DataFrame to numpy array\nX_train, y_train, X_valid, y_valid = train_valid_split(train_data, train_labels) # Splitting the train data into train-valid data\nX_test = process_test_data(test_data) # Converting DataFrame to numpy array\n\nmodel = baselineLSTM(cfg) # Replace this with model = <your model name>(cfg)\nif cfg[\'cuda\']:\n    computing_device = torch.device("cuda")\nelse:\n    computing_device = torch.device("cpu")\nmodel.to(computing_device)\n\ntrain(model, X_train, y_train, X_valid, y_valid, cfg) # Train the model\noutputs = generate(model, X_test, cfg) # Generate the outputs for test data\nsave_to_file(outputs, out_fname) # Save the generated outputs to a file\n'

In [6]:
# loads the train data
dataset = load_data("Beeradvocate_Train_Short.csv")
print (dataset.shape)

# full data set has 1269291 reviews

(1001, 14)


In [7]:
# selects the data that will be used
dataset = dataset[['beer/style', 'review/overall', 'review/text']]
print (dataset.shape)

(1001, 3)


In [8]:
# drops the rows with missing data
dataset.replace('', np.nan, inplace = True)
dataset.dropna(inplace = True)
dataset.reset_index(drop = True, inplace = True)
print (dataset.shape)

# full data dropped 291 rows -- count = 1269000

(1001, 3)


In [9]:
# cleans the data
dataset['beer/style'] = dataset['beer/style'].str.lower()
dataset['review/text'] = dataset['review/text'].str.lower()

char_list = string.ascii_lowercase + string.digits + '!$\'()*,-.:;? '

# converts all whitespace (space, tabs, newlines, etc.) into spaces
whitespace_regex = '[' + string.whitespace + ']'
dataset['review/text'] = dataset['review/text'].str.replace(whitespace_regex, ' ', regex = True)

# removes all invalid characters
invalid_char_regex = '[^' + char_list + ']'
dataset['review/text'] = dataset['review/text'].str.replace(invalid_char_regex, '', regex = True)

In [10]:
# creates lists of beer style and characters for a one-hot encoding
beer_list = dataset['beer/style'].unique()
beer_to_index = dict(zip(beer_list, range(beer_list.shape[0])))
char_to_index = dict(zip(list(char_list), range(len(char_list))))

print ("Number of unique beers: " + str(beer_list.shape[0]))
print ("Number of valid characters: " + str(len(char_list)))

# full dataset: 104

Number of unique beers: 35
Number of valid characters: 49


In [11]:
# updates the configurations for input dimensions
cfg['input_dim'] = beer_list.shape[0] + 1 + cfg['output_dim']

In [12]:
# converts the input features into a one-hot encoding
# result is a numpy array of features (one-hot) and a parallel numpy array of reviews (text)
num_data = dataset.shape[0]                   # number of data points in the dataset
input_feature_length = beer_list.shape[0] + 1 # one-hot encoding of beer style + rating

# converts the input features into a one-hot encoding
input_features = np.zeros((num_data, input_feature_length))
labels = dataset['review/text'].values

for index, review in dataset.iterrows():
    beer_style = review['beer/style']
    beer_index = beer_to_index[beer_style]
    score = review['review/overall']
    
    input_features[index][beer_index] = 1
    input_features[index][-1] = score

In [13]:
# splits the dataset into training and validation sets
percent_training = 0.8

training_last_index = int(percent_training * num_data)

x_train = input_features[:training_last_index]
y_train = labels[:training_last_index]

x_valid = input_features[training_last_index:]
y_valid = labels[training_last_index:]

In [14]:
# loads the test data
dataset_test = load_data("Beeradvocate_Test.csv")
print (dataset_test.shape)

# full dataset: (317323, 13)

(317323, 13)


In [15]:
# selects the data that will be used
dataset_test = dataset_test[['beer/style', 'review/overall']]
print (dataset_test.shape)

(317323, 2)


In [16]:
# cleans the data
dataset_test['beer/style'] = dataset_test['beer/style'].str.lower()

In [17]:
# converts the input features into a one-hot encoding
# result is a numpy array of features (one-hot)
num_data_test = dataset_test.shape[0]   # number of data points in the dataset

# converts the input features into a one-hot encoding
x_test = np.zeros((num_data_test, input_feature_length))

for index, review in dataset_test.iterrows():
    beer_style = review['beer/style']
    beer_index = beer_to_index[beer_style]
    score = review['review/overall']
    
    x_test[index][beer_index] = 1
    x_test[index][-1] = score

KeyError: 'english pale ale'

In [19]:
# trains the model

train_loss = []
valid_loss = []

start = time.time()

if torch.cuda.is_available():
    computing_device = torch.device("cuda")
    cfg['cuda'] = True
    
else:
    computing_device = torch.device("cpu")
    cfg['cuda'] = False

model = bGRU(cfg).to(computing_device)
optimizer = optim.Adam(model.parameters(), cfg['learning_rate'])
criterion = nn.CrossEntropyLoss()
softmax = nn.LogSoftmax()

early_stop_count = 0
min_loss = 100
    
for epoch in range(1, cfg['epochs'] + 1):
    
    print ('----- Epoch #' + str(epoch) + ' -----')
    
    start_index = 0
    end_index = cfg['batch_size']
    
    losses = []
    
    print ('----- Training -----')
    while start_index < len(x_train):
        # takes the minibatch subset
        batch_x = x_train[start_index:end_index]
        batch_y = y_train[start_index:end_index]
        
        # converts the reviews char -> index
        indexed_reviews = [[char_to_index[c] for c in review] for review in batch_y]
        
        # pads the reviews
        padded_reviews = pad_data(indexed_reviews)
        
        # converts the review to a one-hot encoding
        # and concatenates this to the input features
        one_hot_length = len(cfg['char_list']) + 3
        final_batch_x = []
        for features, reviews in zip(batch_x, padded_reviews):
            for char_index in reviews:
                one_hot_encoding = np.zeros(one_hot_length)
                one_hot_encoding[char_index] = 1
                final_features = np.hstack((features, one_hot_encoding))
                final_batch_x.append(final_features)
                
        # converts the final array into a numpy array
        final_batch_x = np.array(final_batch_x)
        
        # reshapes the flattened array into batch_size x sequence_length x feature_length
        final_batch_x.resize(cfg['batch_size'], padded_reviews.shape[1], final_batch_x.shape[1])
        
        # converts final input array to tensors
        final_batch_x = torch.from_numpy(final_batch_x).float().to(computing_device)
              
        # zeros the gradients
        optimizer.zero_grad()
        
        # passes the final input array to the model's forward pass
        outputs, _ = model(final_batch_x)
        soft_outputs = softmax(outputs)
        
        # prints the actual reviews vs the predicted reviews
        if epoch >= 1:
            for i in range(cfg['batch_size']):
                actual_review = batch_y[i]
                predicted_review = ''.join([cfg['char_list'][torch.argmax(x)] 
                                            if torch.argmax(x) < len(cfg['char_list']) 
                                            else '' for x in soft_outputs[i]])

                print ("Actual Review: " + actual_review)
                print ("Predicted Review: " + predicted_review)
        
        # reshapes the outputs to N x feature_length (for the loss function)
        outputs = outputs.view(-1, outputs.shape[2])
        
        # creates the targets and reshapes it to a single dimension
        targets = torch.from_numpy(padded_reviews).long()
        targets = targets.view(-1)
        
        # passes the outputs and targets to the loss function and backpropagates
        loss = criterion(outputs, targets)
        loss.backward()
        optimizer.step()
        
        losses.append(loss.item())
        
        print("Batch start index: " + str(start_index) + " | Loss: " + str(loss.item()))
        print("Time elapsed: " + str(time.time() - start))
        
        start_index = end_index
        end_index += cfg['batch_size']
        if end_index > len(x_train):
            break
        
    
    train_loss.append(np.mean(losses))
    
    
    print ('----- Validating -----')
    start_index = 0
    end_index = cfg['batch_size']
    
    losses = []
    
    with torch.no_grad():
        
        while start_index < len(x_valid):
            # takes the minibatch subset
            batch_x = x_valid[start_index:end_index]
            batch_y = y_valid[start_index:end_index]

            # converts the reviews char -> index
            indexed_reviews = [[char_to_index[c] for c in review] for review in batch_y]

            # pads the reviews
            padded_reviews = pad_data(indexed_reviews)

            # converts the review to a one-hot encoding
            # and concatenates this to the input features
            one_hot_length = len(cfg['char_list']) + 3
            final_batch_x = []
            for features, reviews in zip(batch_x, padded_reviews):
                for char_index in reviews:
                    one_hot_encoding = np.zeros(one_hot_length)
                    one_hot_encoding[char_index] = 1
                    final_features = np.hstack((features, one_hot_encoding))
                    final_batch_x.append(final_features)

            # converts the final array into a numpy array
            final_batch_x = np.array(final_batch_x)

            # reshapes the flattened array into batch_size x sequence_length x feature_length
            final_batch_x.resize(cfg['batch_size'], padded_reviews.shape[1], final_batch_x.shape[1])

            # converts final input array to tensors
            final_batch_x = torch.from_numpy(final_batch_x).float().to(computing_device)

            # passes the final input array to the model's forward pass
            outputs, _ = model(final_batch_x)

            # prints the actual reviews vs the predicted reviews
            if epoch >= 1:
                for i in range(cfg['batch_size']):
                    actual_review = batch_y[i]
                    predicted_review = ''.join([cfg['char_list'][torch.argmax(x)] 
                                                if torch.argmax(x) < len(cfg['char_list']) 
                                                else '' for x in outputs[i]])

                    print ("Actual Review: " + actual_review)
                    print ("Predicted Review: " + predicted_review)

            # reshapes the outputs to N x feature_length (for the loss function)
            outputs = outputs.view(-1, outputs.shape[2])

            # creates the targets and reshapes it to a single dimension
            targets = torch.from_numpy(padded_reviews).long()
            targets = targets.view(-1)

            # passes the outputs and targets to the loss function
            loss = criterion(outputs, targets)

            losses.append(loss.item())

            print("Batch start index: " + str(start_index) + " | Loss: " + str(loss.item()))
            print("Time elapsed: " + str(time.time() - start))

            start_index = end_index
            end_index += cfg['batch_size']
            if end_index > len(x_valid):
                break
            

    average_loss = np.mean(losses)
    valid_loss.append(average_loss)

    # checks for early stopping 
    # early stopping criteria: stops when the validation loss is higher for 3 consecutive epochs
    if average_loss >= min_loss:
        early_stop_count += 1

        if early_stop_count >= 3:
            break

    else:
        early_stop_count = 0
        min_loss = average_loss


----- Epoch #1 -----
----- Training -----
Actual Review: a lot of foam. but a lot. in the smell some banana, and then lactic and tart. not a good start. quite dark orange in color, with a lively carbonation (now visible, under the foam). again tending to lactic sourness. same for the taste. with some yeast and banana.
Predicted Review: ))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))))

Actual Review: according to the website, the style for the caldera cauldron changes every year. the current release is a dipa, which frankly is the only cauldron i'm familiar with (it was an ipadipa the last time i ordered a cauldron at the horsebrass several years back). in any event... at the horse brass yesterday.  the beer pours an orange copper color with good head retention and lacing. the nose is all hoppy ipa goodness, showcasing a huge aroma of dry citrus, pine and sandlewood. the flavor profile replicates the nose pretty closely in this west coast all the way dipa. this dipa is not for the faint of heart and is a bit much even for a hophead like myslf. the finish is quite dry and hoppy, and there's barely enough sweet malt to balance and hold up the avalanche of hoppy bitterness in this beer. mouthfeel is actually fairly light, with a long, persistentely bitter finish. drinkability is good, with the alcohol barely noticeable in this well crafted beer. still, this beer is so h

Actual Review: bottle says malt beverage brewed with ginger and ginger added sounds redundant to me, but lets move on.  pours a bud light yellow with a tiny white head of small bubbles. the beer is almost as clear as a glass of water with some food coloring in it.  aroma of light ginger, a very light malt aroma but primarily odorless on the malt side. i wouldn't be completely surprised if there were some adjuncts in here because of the lack of underlying malt flavors. taste is of a light adjunct lager with a dosing of ginger. not surprising there.   this is a light session beer, good for the warmer days of spring  summer. mouthfeel is extremely light, high carbonation.  overall decent. this would be great if you were drinking beers on draft at the bar with some friends just hanging out. i wouldn't necessarily seek it out though to drink out of a bottle.
Predicted Review: ???????????u?u??????aaaa????aaaaaaa??????????????a?????????uaa??a???a?aaaaaua????aaaaaaaaa?aaaaa???aaaaa????uaaa???a

Actual Review: ok, so the only reason i bought this while shopping at whole foods was because i've never had a ginger beer unless it was ginger ale...and we all know that's not the kind of beer we're interested in on this site! i was very excited to try this one!...  when poured out it looks like a cheapo macro lager at first sight, then the slowly fading head suggests otherwise. the body is crystal clear and is a very light straw color. the head is bright white and slowly dissipates, but is initially quite thick.  smell is adjuncty, but there are slight notes of honey and some kind of herby thing going on...ginger perhaps? can't really tell. from the smell there is obviously something different about this beer though. it has a unique spicy smell to it and reminds me a lot of basil, not ginger. i really can't quite place everything that i smell, but it is a very nice aroma. superb fragrance for this beer, though definitely not a ginger beer based on the smell.  the taste is very unique

Actual Review: brown in color, somewhere between a porter and a brown ale. lacking in aroma, but no off stuff.   same with the taste, lacking flavor, complexity, just went with smoothness. no off flavors though, so i can't say this is bad, just unadventurous, especially for caldera, whom i think is generally underrated. you really have to search to pull anything out of this in terms of the usual chocolatecoffee flavors, really, the only thing i can tell is that the oats did their job, because this is smooth and unoffensive.  other than that, extremely pedestrian.
Predicted Review: ??????????????????????????????????????????????????uu????????????????????????????????????u?u??uuu?????????????????????????????????????????????????????????????????u?????????u????????u??u????uu???u??????u???????????????????????????????????????u??u??????????????????????????????????u????????????????????uuu??????????????u???????????????????????????????u???????????????????u???????????uu????uu?????u?????????????u????

...

Actual Review: purchased at the spar chain grocery store in church stretton, shropshire (where i got plenty of other welsh bottled beers!); bottle-conditioned in a 500ml brown bottle, bb 190509, served cool in a straight imperial pint glass.  a: dark reddish amber in colour, the carbonation comes very light and quiet, supporting an equally restricted thin sheet of off-white foam. s: besides the dominant influence of yeastiness, traditional aroma of golding-like tangerine-ish fruity hoppiness intertwines with raw-ish nuttiness, boiled root veggie, herbal tea and a touch of brown sugar. very light and quiet in terms of aroma. t: a lightly sour-sweet yeasty foretaste backed by powdery biscuity malts, boiled kidney beans and brown malts is ensued by a slightly chewy, ground-root-herb-like bitter-sweetness with a wee bit of spice. restrained in hop-bitterness in the end while the lightly sour  faintly smoky (a tad phenolic) yeastiness also lingers. simplistic. md: quite smooth but slightly 

Actual Review: sampled 532011 at the brewpub.   this was made for the millennium originally but it's been made again, and who knows, in another decade it might be made yet again. so for now i've listed it as rotating. as for the style, all i was told was that it's been burtonized and it has some obvious oak influences.   pours clear, golden brown, small white head that doesnt lace or last.   aroma is wood, sweet, malt, and cherry. kind of barleywine-ish.  flavor is cherry, french oak, a little bit tart, caramel, plum, maybe some bready malts, some old hops (fish food), and low bitterness.   body is slgihtly more than medium, not a ton of co2 but it works. drinkable and enjoyable.   c.
Predicted Review: 
Actual Review: sampled 532011 at the brewpub.   pours hazy yellow, some white head, a tiny bit of lacing but not any real retention.  aroma is honey, grass, a touch of pine, and a bit of bread.  flavor is honey, a touch of corn, some sweet malt, and a little grass, with that buttery bac

Batch start index: 96 | Loss: 1.8298983573913574
Time elapsed: 1314.3199803829193
Actual Review: on-tap at pacific coast  a: the pour is amber in color, not surprisingly, with a decent khaki colored head.  s: not a very pleasant aroma, i must say. there's definitely some sweetness, which is the nicest thing i can say about this beer. there's some sweaty butt crack aroma and quite a bit of alcohol as well.  t: at least this doesn't taste like ass crack (at least, i don't think it does). decently bitter with some grapefruit juice but also some cleaning solution (maybe lemon pledge?). a bit of toffee malt flavor, too.  m: the body is medium and so is the carbonation.  d: just bad. i had thought that the grey whale and megalodon were the bottom of the barrel, but this is certainly in the running.
Predicted Review: 
Actual Review: color is closer to a red then anything  white ring head  bite on the tongue as you drink it. there is kick to it as it drinks on. they say 7. finially a pacific b

Actual Review: amstel strong. 7.5. 0.5 l can.  honey coloured, with a finger of fluffy head. mild carbonation in this clear pilsner. smell is very ok: grassy hops and malts. especially the hops are decent. taste is a bit ordinary, it doesn't deliver upon the smell: it's very malty and sugary sweet. it does have a reasonable hop flavour: grassy and peppery. mouthfeel is medium bodied: the alcohol is well hidden, making it ok drinkable too.  this strong lager is actually not bad at all.
Predicted Review: 
Batch start index: 128 | Loss: 2.8646059036254883
Time elapsed: 1315.504157781601
Actual Review: toffee, raisin and metal aroma; very sweet taste with toffee and pear aromas; sweet finish with pear aroma. pleasantly fruity aroma, ok in the mouth but very thin finish. actually better than most of amstels full-strength lagers.  bitterness 14 ebu, colour 120 ebc.
Predicted Review: 
Actual Review: i had this 'beer' at a beachbar in ijmuiden today. had to drive back home so i needed somethin

Actual Review: pours clear and quite pale from a 12 oz. bottle. a hard to obtain cap of foam settles quickly as large bubbles pop away. a light carbonation from the bottom of the glass weakens in short order.  nose is light overall, offering uncooked grain sense to it yet without metallic or vegetal notes to speak of. slim hint of hops.  flavor is thin, light, watery. particularly as the carbonation dissipates. tastes better directly from the bottle with a touch of carbonation and a light grainyfruity finish. feel is flat and watery in either case. fairly drinkable as it doesn't offend yet has not character whatsoever to justify the concept.
Predicted Review: 
Actual Review: never mind me - i'm just doing the can can on veterans' day! can you dig it?  my pour netted a little better than a finger's worth of bubbly, rocky bone-white head with low retention. the color was a light golden-yellow with ne-quality clarity. nose had a slight grassiness underlain by a cereal quality. mouthfeel w

In [ ]:
y_valid